#  Approximate  analytical protein distribution

(c) 2017 Manuel Razo. This work is licensed under a [Creative Commons Attribution License CC-BY 4.0](https://creativecommons.org/licenses/by/4.0/). All code contained herein is licensed under an [MIT license](https://opensource.org/licenses/MIT). 

In [1]:
import glob
# Our numerical workhorses
import numpy as np
import scipy.optimize
import scipy.special
import scipy.integrate
from sympy import mpmath
import pandas as pd
# Import libraries to parallelize processes
from joblib import Parallel, delayed

# Import matplotlib stuff for plotting
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib as mpl

# Seaborn, useful for graphics
import seaborn as sns

# Import the utils for this project
import chann_cap_utils as chann_cap

# Set PBoC plotting style
chann_cap.set_plotting_style()

# Magic function to make matplotlib inline; other style specs must come AFTER
%matplotlib inline

# This enables SVG graphics inline (only use with static plots (non-Bokeh))
%config InlineBackend.figure_format = 'svg'

figdir = '../../fig/approximate_protein_dist/'
tmpdir = '../../tmp/'

##  Setting up the problem

Given the computationally expensive hypergeometric distribution needed to evaluate the full protein distribution that Shahrezaei and Swain propose it is worth trying some useful aproximations.

In the paper Swain explains that under certain conditions the distribution recovers a negative binomial form (the solution to the two stage promoter). Specifically when both $r_m$ and $r_p$ are fast, then we recover the negative binomial distribution of the form
\begin{equation}
P(p) \rightarrow \frac{\Gamma (\alpha + p)}{\Gamma(p + 1)\Gamma (\alpha)}\left( \frac{b}{1 + b} \right)^p \left( 1 - \frac{b}{1 + b} \right)^\alpha,
\end{equation}
with $\alpha \equiv \frac{k_{off} / \gamma_p \cdot a}{k_{off} / \gamma_p + k_{on} / \gamma_p}$. Taking the log of this equation gives

\begin{equation}
\ln P(p) \rightarrow \ln\Gamma (\alpha + p) - \ln (p + 1) - \ln (\alpha) + p \ln \left( \frac{b}{1 + b} \right)  + \alpha \ln \left( 1 - \frac{b}{1 + b} \right).
\end{equation}

In this notebook we will compare this simplified form with the full distribution to see of this simplified form would be enough for our purposes.

Let's first define a function that computes this log distribution.

In [76]:
def approx_log_p_p_mid_C(C, protein, rep, ka, ki, epsilon, kon, k0, 
                         gamma_m, r_gamma_m, gamma_p, r_gamma_p, logC=False):
    '''
    Computes the approximate log conditional probability lnP(p|C,R), 
    i.e. the probability of having p proteins given 
    an inducer concentration C and a repressor copy number R.
    
    Parameters
    ----------
    C : array-like.
        Concentration at which evaluate the probability.
    protein : array-like.
        protein copy number at which evaluate the probability.        
    repressor : float.
        repressor copy number per cell.
    ki, ka : float.
        dissociation constants for the inactive and active states respectively
        in the MWC model of the lac repressor.
    epsilon : float.
        energetic barrier between the inactive and the active state.
    kon : float.
        rate of activation of the promoter in the chemical master equation
    k0 : float.
        diffusion limited rate of a repressor binding the promoter
    gamma_m : float.
        half-life time for the mRNA.
    r_gamma_m : float.
        average number of mRNA in the unregulated promoter.
    gamma_p : float.
        half-life time for the protein.
    r_gamma_p : float.
        average number of protein per mRNA in the unregulated promoter.
    logC : Bool.
        boolean indicating if the concentration is given in log scale. If True
        C = 10**C
    Returns
    -------
    log probability lnP(p|c,R)
    '''
    # Convert C and mRNA into np.arrays
    C = np.array(C)
    protein = np.array(protein)
    
    # Convert from log if necessary
    if logC:
        C = 10**C
 
    # Calculate the off rate including the MWC model
    koff = k0 * rep * chann_cap.p_act(C, ka, ki, epsilon)

    # compute the variables needed for the distribution
    a = r_gamma_m * gamma_m / gamma_p # r_m / gamma_p
    b = r_gamma_p * gamma_p / gamma_m # r_p / gamma_m
    gamma = gamma_m / gamma_p
    Kon = kon / gamma_p
    Koff = koff / gamma_p
    
    alpha = Kon * a / (Kon + Koff)
    
    # Compute the probability
    lnp = scipy.special.gammaln(alpha + protein) \
    - scipy.special.gammaln(protein + 1) \
    - scipy.special.gammaln(alpha) \
    + protein * (np.log(b) - np.log(1 + b)) \
    + alpha * np.log(1 - b / (1 + b)) \
    
    return lnp.astype(float)[0]

Once we have the function, let's test it with our current parameters.

First let's deifne all the parameters we will need.

In [22]:
# Define a dictionary that contains relevant parameters
energies = {'O1':-15.3, 'O2':-13.9, 'O3':-9.7, 'Oid':-17}
rbs = np.array(['RBS1L', 'RBS1', 'RBS1027', 'RBS446', 'RBS1147', 'HG104'])
repressors = dict(zip(rbs,[870, 610, 130, 62, 30, 11]))

# Define experimental IPTG concentrations
c = [0, 0.1, 5, 10, 25, 50, 75, 100, 250, 500, 1000, 5000] # µM

# Define the MWC dissociation constants
mwc_param = dict(ka=139.55, ki=0.53, epsilon=4.5)

# Define the CME parameters
k0 = 0.0001347
prot_params = dict(ka=139.55, ki=0.53, epsilon=4.5,
                   gamma_m=0.00284, r_gamma_m=15.7,
                   gamma_p=0.000277, r_gamma_p=100,
                   k0=k0)

For the full distributions we will the pre-computed lookup tables since the computation can take quite some time.

In [4]:
df_prob = pd.read_csv('../../data/csv_protein_dist/lnp_' + 'O2' + \
                              '_all_RBS1027_fit.csv',
                              header=0, index_col=0, comment='#')

In [59]:
# Extract input-ouput relationship
QpC = chann_cap.theory_trans_matrix(df_prob, c, 260, clean=False, **mwc_param)
p_grid = np.arange(0, np.shape(QpC)[1])

In [28]:
# Define colors
colors = sns.color_palette('Blues', n_colors=len(c))

# Initialize figure
fig, ax = plt.subplots(2, 1, figsize=(6,5), sharex=True)
ax[0].yaxis.set_major_formatter(mpl.ticker.ScalarFormatter(\
                             useMathText=True, 
                             useOffset=False))

# Loop through number of repressors
for i, C in enumerate(c):
    # PMF plot
    ax[0].plot(p_grid, QpC[i, :], drawstyle='steps',
              color='k')
    ax[0].fill_between(p_grid, QpC[i, :], color=colors[i], alpha=0.8,
                      step='pre')
    # CDF plot
    ax[1].plot(p_grid, np.cumsum(QpC[i, :]), drawstyle='steps',
              color=colors[i], linewidth=2)

ax[0].set_ylabel('probability')
ax[0].margins(0.02)
ax[0].ticklabel_format(style='sci', axis='y', scilimits=(0,0))
ax[0].set_ylim(top=1E-2)

ax[1].set_xlabel('number of protein')
ax[1].set_ylabel('CDF')
ax[1].margins(0.02)

# Declare color map for legend
cmap = plt.cm.get_cmap('Blues_r', len(c))
bounds = np.linspace(0, len(c), len(c) + 1)

# Plot a little triangle indicating the mean of each distribution
mean_p = [np.sum(p_grid * prob) for prob in QpC]

mean_plot = ax[0].scatter(mean_p, [6.5E-3] * len(mean_p), marker='v', s=200,
            c=np.arange(len(mean_p)), cmap=cmap,
            edgecolor='k',
            linewidth=1.5)

# Generate a colorbar with the concentrations
cbar_ax = fig.add_axes([0.95, 0.25, 0.03, 0.5])
cbar = fig.colorbar(mean_plot, cax=cbar_ax)
cbar.ax.get_yaxis().set_ticks([])
for j, C in enumerate(c):
    if (C == 0) or (C > 1):
        label=str(int(C))
    else:
        label=str(C)
    cbar.ax.text(1, j / len(c) + 1 / (2 * len(c)),
                 label, ha='left', va='center',
                 transform = cbar_ax.transAxes, fontsize=12)
cbar.ax.get_yaxis().labelpad = 35
cbar.set_label(r'[inducer] ($\mu$M)')

plt.figtext(0.0, .9, 'A', fontsize=20)
plt.figtext(0.0, .46, 'B', fontsize=20)


plt.subplots_adjust(hspace=0.06)

Now let's compute the approximate distribution using the same parameters. To make things simple we will define a function that builds the same type of input-output matrix given a set of parameters and a concentration array.

In [101]:
def approx_trans_matrix(c, protein, Rtot, prot_params, tol=1E-20, clean=True):
    '''
    Function that builds the transition matrix Qg|c for a series of
    concentrations c. It builds the approximate matrix using the negative 
    binomial approximation of the full protein distribution.
    Parameters
    ----------
    c : array-like.
        Concentrations at which to evaluate the input-output function.
    protein : array-like.
        Protein copy numbers at which evaluate the distribution.
    Rtot : float.
        repressor copy number per cell.
    Rtot : int.
        Total number of repressors per cell.
    tol : float.
        tolerance under which if a marginal probability for a protein is
        lower than that, that column is discarded.
    clean : bool.
        Boolean indicating if the entire matrix should be returned or if the
        columns with cumulative probability < tol should be removed.
    kwargs : dict.
        arguments to be passed to the approx_log_p_p_mid_C function
        
        ki, ka : float.
            dissociation constants for the inactive and active states respectively
            in the MWC model of the lac repressor.
        epsilon : float.
            energetic barrier between the inactive and the active state.
        kon : float.
            rate of activation of the promoter in the chemical master equation
        k0 : float.
            diffusion limited rate of a repressor binding the promoter
        gamma_m : float.
            half-life time for the mRNA.
        r_gamma_m : float.
            average number of mRNA in the unregulated promoter.
        gamma_p : float.
            half-life time for the protein.
        r_gamma_p : float.
            average number of protein per mRNA in the unregulated promoter.
        logC : Bool.
            boolean indicating if the concentration is given in log scale. If True
            C = 10**C

    Returns
    -------
    Qg|c : input output matrix in which each row represents a concentration
    and each column represents the probability of a protein copy number.
    '''
    # Convert C and mRNA into np.arrays
    c = np.array(c)
    protein = np.array(protein)
        
    # Extract dictionary with the MWC parameters for the p_act function
    mwc_params = { 'ka', 'ki', 'epsilon'}
    p2 = {key:prot_params[key] for key in prot_params.keys() & mwc_params}
    
    # Initialize matrix to save input-output function
    Qgc = np.zeros([len(c), len(protein)])
    
    # Loop through every repressor and add the probabilities to each
    # row of the Qg|c matrix
    for i, C in enumerate(c):
        # compute the p_active probabilities for each concentration
        pact = chann_cap.p_act(C, **p2)
        # Compute the number of repressors given this p_active. The
        # repressors will be round down for fractional number of repressors
        prot_params['rep'] = np.floor(Rtot * pact)
        Qgc[i, :] = np.exp(approx_log_p_p_mid_C(C, protein, **prot_params))
    
    # Conditional on whether or not to clean the matrix
    if clean:
        # Remove columns whose marginal protein probability is < tol
        prot_marginal = Qgc.sum(axis=0)
        return Qgc[:, prot_marginal > tol]
    else:
        return Qgc

In [119]:
# Define experimental IPTG concentrations
c = [0, 0.1, 5, 10, 25, 50, 75, 100, 250, 500, 1000, 5000] # µM

# Define the CME parameters
k0 = 0.0001347
kon = chann_cap.kon_fn(epsilon=-15.7, k0=k0)
prot_params = dict(ka=139.55, ki=0.53, epsilon=4.5,
                   gamma_m=0.00284, r_gamma_m=15.7,
                   gamma_p=0.000277, r_gamma_p=100,
                   k0=k0, kon=kon)

# Define the protein grid to compute the distribution for
p_grid = np.arange(0, 4000)
aQpC = approx_trans_matrix(c, p_grid, 130, prot_params, clean=False)
np.shape(aQpC)

(12, 4000)

In [120]:
np.sum(aQpC, axis=1)

array([  1.24284916e+002,   1.19085509e+002,   1.40155924e-003,
         1.67400423e-026,   2.05270113e-128,   3.45831379e-158,
         1.06408091e-161,   3.59678566e-163,   3.59678566e-163,
         3.59678566e-163,   3.59678566e-163,   3.59678566e-163])